In [1]:
import xml.etree.cElementTree as ET
import os
import nltk
import string
import random
import pandas as pd
from sklearn.preprocessing import LabelEncoder
from pandas import DataFrame
import nltk.data
from nltk import sent_tokenize

In [2]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 3118758295233955497
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 10193742398
locality {
  bus_id: 1
  links {
  }
}
incarnation: 12543223342730931254
physical_device_desc: "device: 0, name: GeForce GTX TITAN X, pci bus id: 0000:01:00.0, compute capability: 5.2"
]


# Get the files for parsing

## Training Data

In [3]:
codefolder = os.path.dirname(os.path.abspath('__file__'))

datafolders = ['\\data_all\\06_training-RiskFactors-Complete-Set1\\','\\data_all\\09_training-RiskFactors-Complete-Set2\\']
filenames = []

for folder in datafolders:
    for file in os.listdir(str(codefolder)+folder):
        filename=os.fsdecode(os.fsencode((str(codefolder)+folder+file)))
        if filename.endswith(('.xml')):
            filenames.append(filename)
            
filenames[:5]

['E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\06_training-RiskFactors-Complete-Set1\\220-01.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\06_training-RiskFactors-Complete-Set1\\220-02.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\06_training-RiskFactors-Complete-Set1\\220-03.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\06_training-RiskFactors-Complete-Set1\\220-04.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\06_training-RiskFactors-Complete-Set1\\220-05.xml']

In [4]:
# use a 90/10 split
split_index = int(len(filenames)*0.9)
random.seed(42)
random.shuffle(filenames)

train_filenames = filenames[:split_index]
dev_filenames = filenames[split_index:]

In [5]:
train_filenames[:5]

['E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\09_training-RiskFactors-Complete-Set2\\103-01.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\09_training-RiskFactors-Complete-Set2\\109-02.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\09_training-RiskFactors-Complete-Set2\\155-03.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\06_training-RiskFactors-Complete-Set1\\251-03.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\09_training-RiskFactors-Complete-Set2\\107-02.xml']

In [6]:
dev_filenames[:5]

['E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\06_training-RiskFactors-Complete-Set1\\335-03.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\09_training-RiskFactors-Complete-Set2\\149-04.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\06_training-RiskFactors-Complete-Set1\\366-04.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\09_training-RiskFactors-Complete-Set2\\181-02.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\09_training-RiskFactors-Complete-Set2\\180-01.xml']

## Test Data

In [7]:
datafolder = '\\data_all\\16_testing-RiskFactors-Complete\\'
test_filenames = []

for file in os.listdir(str(codefolder)+datafolder):
    filename=os.fsdecode(os.fsencode((str(codefolder)+datafolder+file)))
    if filename.endswith(('.xml')):
        test_filenames.append(filename)

test_filenames[:5]

['E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\16_testing-RiskFactors-Complete\\110-01.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\16_testing-RiskFactors-Complete\\110-02.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\16_testing-RiskFactors-Complete\\110-03.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\16_testing-RiskFactors-Complete\\110-04.xml',
 'E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\data_all\\16_testing-RiskFactors-Complete\\111-01.xml']

# Define function to get sentences & labels

In [8]:
def get_sentences(file):

    tree = ET.ElementTree(file=file)
    root = tree.getroot()

    text = root.find('TEXT').text
    sentences = [sent.split('\n') for sent in sent_tokenize(text) if sent!='\n']
    all_sentences = []

    for item in sentences:
        for sub_item in item:
            if sub_item.replace(' ','') != '':
                all_sentences.append(sub_item)    
    print("all_sentences:",all_sentences[:5])
    return all_sentences

# Function definition for processing a file

In [9]:
def process_file(file):
    
    # get all sentences in the file
    tree = ET.ElementTree(file=file)
    root = tree.getroot()

    text = root.find('TEXT').text
    sentences = [sent.split('\n') for sent in sent_tokenize(text) if sent!='\n']
    all_sentences = []

    for item in sentences:
        for sub_item in item:
            if sub_item.replace(' ','') != '':
                all_sentences.append(sub_item)    
                
    #all_sent = get_sentences(file)
    sent_label = {}

    sub_tags = []
    for item in root.find("TAGS"):
        if item.tag == 'PHI':
            pass
        elif item.tag == 'SMOKER':
            label = (item.tag + "." + item.attrib['status']).lower().replace(" ", "_")
        elif item.tag == 'FAMILY_HIST':
            label = (item.tag + "." + item.attrib['indicator']).lower().replace(" ", "_")
        elif item.tag == 'MEDICATION':
            label = (item.tag + "." + item.attrib['type1'] + "." + item.attrib['type2'] + "." + item.attrib['time']).lower().replace(" ", "_")
        else:
            label = (item.tag + "." + item.attrib['indicator'] + "." + item.attrib['time']).lower().replace(" ", "_")
        for sub_item in item.findall(item.tag):
            print("sub_item:", sub_item.tag)
            if ('text' in sub_item.attrib.keys()):
                print(sub_item.attrib['text'])
                sub_tags.append((sub_item.attrib['text'], label))


    count=0
    for sent in all_sentences:
        label='Other'
        for tag in set(sub_tags):                                                       
            if tag[0] in sent:
                label = tag[1]
                count += 1

        sent_label[sent] = label
        
    # return empty dict if no tag found in file
    # else, return the sentences with the labels
    if count==0:
        return {}
    else:
        return sent_label

In [10]:
def get_TrainingData(filenames):
    train_files = []
    train_sent = []
    train_labels = []

    for file in filenames:
        file_data = process_file(file=file)
        for i in range(0, len(file_data)):
            train_files.append(file)
            
        for key, value in file_data.items():
            train_sent.append(key)
            train_labels.append(value)
    
    train_df = pd.DataFrame({'filename': train_files, 'sentence': train_sent, 'label': train_labels})
    return train_df

# Generate Data for Models

In [11]:
df_train = get_TrainingData(train_filenames)
df_dev = get_TrainingData(dev_filenames)
df_test = get_TrainingData(test_filenames)

sub_item: MEDICATION
aspirin
sub_item: MEDICATION
aspirin
sub_item: MEDICATION
Lopressor
sub_item: MEDICATION
Lopressor
sub_item: HYPERTENSION
Blood pressure 143/96.
sub_item: HYPERTENSION
143/96.
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: SMOKER
 Remote history of smoking.  
sub_item: SMOKER
Remote history of smoking.  
sub_item: DIABETES
non-insulin-dependent diabetes 
sub_item: DIABETES
diabetes
sub_item: DIABETES
diabetes
sub_item: DIABETES
non-insulin-dependent diabetes 
sub_item: DIABETES
diabetes
sub_item: DIABETES
diabetes
sub_item: DIABETES
non-insulin-dependent diabetes 
sub_item: DIABETES
diabetes
sub_item: DIABETES
diabetes
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
aspirin
sub_item: MEDICATION
aspirin
sub_item: MEDICATION
Hctz
sub_item: MEDICATION
Hctz
sub_item: MEDICATION
Hctz
sub_

sub_item: MEDICATION
Glyburide
sub_item: MEDICATION
Lopid
sub_item: MEDICATION
Lopid
sub_item: MEDICATION
Lopid
sub_item: MEDICATION
Propranolol
sub_item: MEDICATION
Propranolol
sub_item: MEDICATION
Propranolol
sub_item: MEDICATION
Propranolol
sub_item: MEDICATION
Propranolol
sub_item: MEDICATION
Propranolol
sub_item: HYPERTENSION
hypertension
sub_item: HYPERTENSION
hypertension
sub_item: HYPERTENSION
hypertension
sub_item: HYPERTENSION
150/90.
sub_item: HYPERTENSION
 150/90
sub_item: HYPERTENSION
blood pressure here is 150/90
sub_item: HYPERTENSION
hypertension
sub_item: HYPERTENSION
hypertension
sub_item: HYPERTENSION
hypertension
sub_item: HYPERTENSION
hypertension
sub_item: HYPERTENSION
hypertension
sub_item: HYPERTENSION
hypertension
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: SMOKER
She does not smoke
sub_item: SMOKER
not smoke
sub_item: SMOKER
does not smoke
sub_item: DIABETES
diabetes
sub_item: DIABETES
diabetes
sub_item: DIABETES
diabetes
sub_it

sub_item: CAD
CAD
sub_item: CAD
CAD
sub_item: CAD
CAD
sub_item: CAD
CAD
sub_item: CAD
CAD
sub_item: CAD
coronary artery disease
sub_item: CAD
CAD
sub_item: CAD
CAD
sub_item: CAD
CAD
sub_item: CAD
CAD
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: SMOKER
 Smoked 1 ppd for many years, but quit 7 years ago
sub_item: SMOKER
Smoked 1 ppd for many years, but quit 7 years ago
sub_item: SMOKER
quit 
sub_item: DIABETES
DM
sub_item: DIABETES
DM
sub_item: DIABETES
DM
sub_item: DIABETES
DM
sub_item: DIABETES
DM
sub_item: DIABETES
DM
sub_item: DIABETES
DM
sub_item: DIABETES
DM
sub_item: DIABETES
DM
sub_item: MEDICATION
Insulin
sub_item: MEDICATION
 Insulin
sub_item: MEDICATION
Insulin
sub_item: MEDICATION
Insulin
sub_item: MEDICATION
 Insulin
sub_item: MEDICATION
Insulin
sub_item: MEDICATION
Insulin
sub_item: MEDICATION
 Insulin
sub_item: MEDICATION
Insulin
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: SMOKER
sub_item: SMOKER
 Record
sub_it

SH
sub_item: DIABETES
DM2
sub_item: DIABETES
DM2
sub_item: DIABETES
DM
sub_item: DIABETES
DM2
sub_item: MEDICATION
PRAVASTATIN
sub_item: MEDICATION
PRAVASTATIN
sub_item: MEDICATION
statin
sub_item: MEDICATION
PRAVASTATIN
sub_item: MEDICATION
PRAVASTATIN
sub_item: MEDICATION
PRAVASTATIN
sub_item: MEDICATION
statin
sub_item: MEDICATION
PRAVASTATIN
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: MEDICATION
LISINOPRIL
sub_item: MEDICATION
LISINOPRIL 
sub_item: MEDICATION
AceI
sub_item: MEDICATION
LISINOPRIL   
sub_item: MEDICATION
 ACETYLSALICYLIC ACID
sub_item: MEDICATION
ACETYLSALICYLIC ACID 
sub_item: MEDICATION
Asa
sub_item: MEDICATION
ACETYLSALICYLIC ACID
sub_item: DIABETES
 GLU 156
sub_item: DIABETES
GLU 268
sub_item: DIABETES
GLU 200
sub_item: DIABETES
GLU 231
sub_item: DIABETES
GLU 268
sub_item: DIABETES
GLU 200
sub_item: DIABETES
GLU 231
sub_item: DIABETES
GLU-POC 209
sub_item: DIABETES
GLU-POC 235
sub_item: DIABETES
GLU-POC 202
sub_item: DIABETES
GLU-P

sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: DIABETES
diabetes
sub_item: DIABETES
diabetes
sub_item: DIABETES
diabetes
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril 
sub_item: MEDICATION
Zocor
sub_item: MEDICATION
Zocor
sub_item: MEDICATION
Zocor
sub_item: MEDICATION
Aspirin
sub_item: MEDICATION
Aspirin
sub_item: MEDICATION
Aspirin
sub_item: MEDICATION
Metformin
sub_item: MEDICATION
Metformin
sub_item: MEDICATION
Metformin
sub_item: MEDICATION
Metformin
sub_item: MEDICATION
Metformin
sub_item: MEDICATION
Metformin
sub_item: HYPERTENSION
HTN
sub_item: HYPERTENSION
HTN
sub_item: HYPERTENSION
HTN
sub_item: DIABETES
DMT2
sub_item: DIABETES
DMT2
sub_item: DIABETES
DM
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril 
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril 
sub_item: DIABETES
DMT2
sub_item: DIABETES
DMT2
sub_it

...

sub_item: MEDICATION
Monopril 
sub_item: MEDICATION
Monopril 40 mg q.d
sub_item: MEDICATION
Monopril
sub_item: MEDICATION
Dyazide 
sub_item: MEDICATION
Dyazide 1 q.d.
sub_item: MEDICATION
Glynase
sub_item: MEDICATION
Glynase 3 mg q.a.m
sub_item: MEDICATION
Glynase
sub_item: MEDICATION
Glucophage
sub_item: MEDICATION
Glucophage 500 mg q.p.m
sub_item: MEDICATION
Glucophage
sub_item: MEDICATION
Glucophage
sub_item: MEDICATION
Glucophage 500 mg q.p.m
sub_item: MEDICATION
Glucophage
sub_item: MEDICATION
Dyazide 
sub_item: MEDICATION
Dyazide 1 q.d.
sub_item: MEDICATION
Monopril 
sub_item: MEDICATION
Monopril 40 mg q.d
sub_item: MEDICATION
Monopril
sub_item: MEDICATION
Glucophage
sub_item: MEDICATION
Glucophage 500 mg q.p.m
sub_item: MEDICATION
Glucophage
sub_item: MEDICATION
Monopril 
sub_item: MEDICATION
Monopril 40 mg q.d
sub_item: MEDICATION
Monopril
sub_item: MEDICATION
Glynase
sub_item: MEDICATION
Glynase 3 mg q.a.m
sub_item: MEDICATION
Glynase
sub_item: MEDICATION
Dyazide 
sub_item: ME

sub_item: DIABETES
diabetes
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: HYPERLIPIDEMIA
Elevated cholesterol
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: HYPERLIPIDEMIA
Elevated cholesterol
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: HYPERLIPIDEMIA
Elevated cholesterol
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: HYPERLIPIDEMIA
hypercholesterolemia
sub_item: MEDICATION
Diltiazem 60mg qd
sub_item: MEDICATION
Diltiazem
sub_item: MEDICATION
Diltiazem
sub_item: MEDICATION
Lipitor 10mg qd 
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Lipitor 
sub_item: MEDICATION
Lipitor 10mg qd 
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Lipitor 
sub_item: MEDICATION
Lipitor 10mg qd 
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Lipitor 
sub_item: MEDICATION
Diltiaz

sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: SMOKER
sub_item: SMOKER
sub_item: SMOKER
Record 
sub_item: HYPERLIPIDEMIA
HL
sub_item: HYPERLIPIDEMIA
HL
sub_item: HYPERLIPIDEMIA
HL
sub_item: HYPERLIPIDEMIA
HL
sub_item: HYPERLIPIDEMIA
HL
sub_item: HYPERLIPIDEMIA
HL
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Niacin
sub_item: MEDICATION
Niacin
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
Plavix
sub_item: MEDICATION
Plavix 
sub_item: MEDICATION
Plavix
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Nifedipine
sub_item: MEDICATION
Plavix
sub_item: MEDICATION
Plavix 
sub_item: MEDICATION
Plavix
sub_item: MEDICATION
Niacin
sub_item: MEDICATION
Niacin
sub_item:

sub_item: HYPERLIPIDEMIA
Her LDL is 116
sub_item: HYPERLIPIDEMIA
Her LDL is 116 ono 2/87 
sub_item: HYPERLIPIDEMIA
LDL is 116
sub_item: OBESE
OBESITY : Type 3
sub_item: OBESE
OBESITY
sub_item: OBESE
OBESITY
sub_item: OBESE
OBESITY : Type 3
sub_item: OBESE
OBESITY
sub_item: OBESE
OBESITY
sub_item: OBESE
OBESITY : Type 3
sub_item: OBESE
OBESITY
sub_item: OBESE
OBESITY
sub_item: OBESE
obese
sub_item: OBESE
BMI 44 
sub_item: OBESE
BMI 44
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lisinopril
sub_item: MEDICATION
Lipitpr
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Restart Lipitor 
sub_item: MEDICATION
Lipitor
sub_item: MEDICATION
Ecasa
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
Ecasa
sub_item: MEDICATION
Ecasa
sub_item: MEDICATION
Metformin
sub_item: MEDICATION
Metformin
sub_item: MEDICATION
Metfo

sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: FAMILY_HIST
sub_item: SMOKER
Record 
sub_item: SMOKER
sub_item: SMOKER
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
ASA,
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ECASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA,
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ECASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
Losartan
sub_item: MEDICATION
Losartan
sub_item: MEDICATION
Losartan
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
Simvastatin
sub_item: MEDICATION
ASA,
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ECASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
ASA
sub_item: MEDICATION
Losartan
sub_item: MEDICATION
Losartan
sub_item: MEDICATION
Losartan
sub_item: MEDI

# Write Data to Files

In [12]:
le = LabelEncoder()

# refer (https://blog.insightdatascience.com/using-bert-for-state-of-the-art-pre-training-for-natural-language-processing-1d87142c29e7)

# get the training set for BERT in the required format
df_train_bert = pd.DataFrame({'user_id':df_train.index,
            'label':le.fit_transform(df_train['label']),
            'alpha':['a']*df_train.shape[0],
            'text':df_train['sentence'].replace(r'\n',' ',regex=True)})


# get the dev set for BERT in the required format
df_dev_bert = pd.DataFrame({'user_id':df_dev.index,
            'label':le.fit_transform(df_dev['label']),
            'alpha':['a']*df_dev.shape[0],
            'text':df_dev['sentence'].replace(r'\n',' ',regex=True)})


 # Creating test dataframe according to BERT (CoLA Format)
df_test_bert = pd.DataFrame({'id':df_test.index,
                 'sentence':df_test['sentence'].replace(r'\n',' ',regex=True)})

In [13]:
df_train_bert.to_csv('E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\SENT_Single_Model\\train.tsv', sep='\t', index=False, header=False)
df_dev_bert.to_csv('E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\SENT_Single_Model\\dev.tsv', sep='\t', index=False, header=False)
df_test_bert.to_csv('E:\\Google Drive\\Berkeley\\Courses\\w266_NLP\\Final Project\\SENT_Single_Model\\test.tsv', sep='\t', index=False, header=True)

In [14]:
df_train_bert['label'].unique()

array([ 0, 15, 26, 42, 90, 40, 28, 50, 69, 32, 44, 24, 88, 17, 29, 70,  5,
       22,  4, 75, 57, 11,  3, 27, 58, 62,  1, 61, 73, 86, 72, 39, 43, 78,
       20, 68, 65, 83, 66, 41, 79, 30, 67, 31, 71, 48, 23, 56, 84, 35, 47,
       13, 80, 74, 85, 21,  9, 89, 25, 60, 49, 16, 46, 45, 34, 14,  7, 18,
       12, 59, 10, 64, 53, 76, 87, 33, 36,  8, 52, 37,  2, 19, 77, 38, 82,
       51,  6, 54, 55, 63, 81], dtype=int64)